In [1]:
import pandas as pd
import plotly.express as px
import json
import scipy


In [2]:
no_camera_case = 'imu_output_static-no-camera_20240326-071836.txt'
camera_case = 'imu_output_static-camera_20240326-072828.txt'

filedata = None

with open(no_camera_case, 'r') as f:
    filedata = f.readlines()
    
# Create a pandas dataframe
df = pd.DataFrame( columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-quaternion', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])
accumulator = []

# max_lines = 1000
# counter = 0
for line in filedata:
    try:
        # counter += 1
        #split by tab
        tokens = line.split('   ')
        timestamp = tokens[0]
        data = tokens[1]
        data = json.loads(data)
        quat = data['imu']['083A8DCCC2F4']['quaternion']
        #convert quat to euler
        quat = [quat['w'], quat['x'], quat['y'], quat['z']]
        euler = scipy.spatial.transform.Rotation.from_quat(quat).as_euler('xyz', degrees=True)
        accumulator.append([timestamp, quat, euler[0], euler[1], euler[2]])
        # if counter >= max_lines:
        #     break
    except Exception as e:
        print(e)
        print(line)
        break
    
df = pd.concat([df, pd.DataFrame(accumulator, columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z'])], ignore_index=True)
display(df)

timestamp                                     imu-quaternion  \
0       752236.1718874  [0.99998939, 0.002357125, -0.013809504, -0.001...   
1       752236.1752317  [0.999990463, 0.002190262, -0.01382183, -0.001...   
2       752236.1767906  [0.999990344, 0.002019376, -0.013820686, -0.00...   
3       752236.1797802  [0.999989986, 0.001876712, -0.01381807, -0.001...   
4       752236.1818813  [0.999990344, 0.001756668, -0.013815911, -0.00...   
...                ...                                                ...   
195960  752764.4013491  [0.998346686, 0.002081305, -0.058845498, -0.00...   
195961  752764.4037216  [0.998346329, 0.002240747, -0.058845676, -0.00...   
195962   752764.405558  [0.998352647, 0.002112269, -0.058846388, -0.00...   
195963  752764.4082064  [0.998352647, 0.001972079, -0.058849182, -0.00...   
195964  752764.4105381  [0.998353064, 0.001831472, -0.058848955, -0.00...   

        imu-euler-x  imu-euler-y  imu-euler-z camera-quaternion  \
0       -179.855306     1.582025     0.272107               NaN   
1       -179.833764     1.583412     0.253285               NaN   
2       -179.828261     1.583298     0.233778               NaN   
3       -179.832146     1.583031     0.217376               NaN   
4       -179.841745     1.582820     0.203487               NaN   
...             ...          ...          ...               ...   
195960  -179.846617     6.746229     0.247935               NaN   
195961  -179.857482     6.746253     0.265596               NaN   
195962  -179.863414     6.746324     0.250498               NaN   
195963  -179.869784     6.746676     0.234032               NaN   
195964  -179.875542     6.746676     0.217553               NaN   

       camera-euler-x camera-euler-y camera-euler-z  
0                 NaN            NaN            NaN  
1                 NaN            NaN            NaN  
2                 NaN            NaN            NaN  
3                 NaN            NaN            NaN  
4                 NaN            NaN            NaN  
...               ...            ...            ...  
195960            NaN            NaN            NaN  
195961            NaN            NaN            NaN  
195962            NaN            NaN            NaN  
195963            NaN            NaN            NaN  
195964            NaN            NaN            NaN  

[195965 rows x 9 columns]

In [3]:
# subtract the average from each axis
df_mod = df.copy()
#delete the first 1000 samples
df_mod = df_mod[6000:]
#limit to 10000 samples
df_mod = df_mod[:10000]
#convert timestamp from float to 
#time was timestamp = time.perf_counter()
df_mod['timestamp'] = pd.to_datetime(df_mod['timestamp'], unit='s')
#convert all values to float
df_mod['imu-euler-x'] = df_mod['imu-euler-x'].astype(float)
df_mod['imu-euler-y'] = df_mod['imu-euler-y'].astype(float)
df_mod['imu-euler-z'] = df_mod['imu-euler-z'].astype(float)


# get the average for each axis in euler
imu_euler_x_avg = df_mod['imu-euler-x'].mean()
imu_euler_y_avg = df_mod['imu-euler-y'].mean()
imu_euler_z_avg = df_mod['imu-euler-z'].mean()
df_mod['imu-euler-x'] = df_mod['imu-euler-x'] - imu_euler_x_avg
df_mod['imu-euler-y'] = df_mod['imu-euler-y'] - imu_euler_y_avg
df_mod['imu-euler-z'] = df_mod['imu-euler-z'] - imu_euler_z_avg

# plot 3 axis in the same plot
fig = px.line(df_mod, x='timestamp', y=['imu-euler-x', 'imu-euler-y', 'imu-euler-z'])
fig.show()
#save fig as html
plot_name = 'imu_euler_no_camera.html'
fig.write_html(plot_name)

In [4]:
#plot the histogram of each axis
for axis in ['imu-euler-x', 'imu-euler-y', 'imu-euler-z']:
    fig = px.histogram(df_mod, x=axis, nbins=100)
    fig.show()
    plot_name = f'{axis}_histogram_no_camera.html'
    fig.write_html(plot_name)
    

In [5]:


filedata = None

with open(camera_case, 'r') as f:
    filedata = f.readlines()
    
# Create a pandas dataframe
df = pd.DataFrame( columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-quaternion', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])
accumulator = []

# max_lines = 10
# counter = 0
for line in filedata:
    try:
        #split by tab
        tokens = line.split('   ')
        timestamp = tokens[0]
        data = tokens[1]
        data = json.loads(data)
        if 'camera' in data and data['camera'] is not None:
            tokens = line.split('   ')
            timestamp = tokens[0]
            data = tokens[1]
            data = json.loads(data)
            imuquat = data['imu']['083A8DCCC2F4']['quaternion']
            #convert quat to euler
            imuquat = [imuquat['w'], imuquat['x'], imuquat['y'], imuquat['z']]
            #get camera data
            camquat = data['camera']['16']['quaternion']
            #convert quat to euler
            camquat = [camquat['w'], camquat['x'], camquat['y'], camquat['z']]
            imu_euler = scipy.spatial.transform.Rotation.from_quat(imuquat).as_euler('xyz', degrees=True)
            cam_euler = scipy.spatial.transform.Rotation.from_quat(camquat).as_euler('xyz', degrees=True)
            accumulator.append([timestamp, imuquat, imu_euler[0], imu_euler[1], imu_euler[2], camquat, cam_euler[0], cam_euler[1], cam_euler[2]])
            # counter += 1
            # if counter >= max_lines:
            #     break
    except Exception as e:
        print(f"Error: {e}")
        break
    
df = pd.concat([df, pd.DataFrame(accumulator, columns=['timestamp', 'imu-quaternion', 'imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-quaternion', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])], ignore_index=True)
display(df)

Error: list index out of range


timestamp                                     imu-quaternion  \
0      752829.6709815  [1.000076175, 0.002650619, -0.001048881, 0.001...   
1      752829.6713583  [1.000076175, 0.002650619, -0.001048881, 0.001...   
2      752829.6724912  [1.00008285, 0.002632231, -0.001047024, 0.0016...   
3      752829.6770621  [1.000080228, 0.002678126, -0.001042149, 0.001...   
4      752829.6812662  [1.000080109, 0.002726376, -0.001038534, 0.001...   
...               ...                                                ...   
11760  752863.8825753  [0.985049248, 0.169484764, -0.001508256, -0.03...   
11761  752863.8869862  [0.985060513, 0.169408739, -0.001504578, -0.03...   
11762  752863.8879648  [0.985069752, 0.169355363, -0.001508368, -0.03...   
11763  752863.8922492  [0.985071301, 0.169341654, -0.001505136, -0.03...   
11764   752863.895236  [0.985065758, 0.169369757, -0.001507159, -0.03...   

       imu-euler-x  imu-euler-y  imu-euler-z  \
0       179.797934     0.120719     0.303502   
1       179.797934     0.120719     0.303502   
2       179.815370     0.120456     0.301412   
3       179.841435     0.119836     0.306699   
4       179.867492     0.119359     0.312256   
...            ...          ...          ...   
11760  -176.179442    -0.481591    19.509060   
11761  -176.181026    -0.481446    19.500263   
11762  -176.182310    -0.480574    19.494087   
11763  -176.182470    -0.480869    19.492499   
11764  -176.181967    -0.480832    19.495781   

                                       camera-quaternion  camera-euler-x  \
0      [0.977991372328468, 0.20481141277070392, -0.00...     -175.486833   
1      [0.977991372328468, 0.20481141277070392, -0.00...     -175.486833   
2      [0.977991372328468, 0.20481141277070392, -0.00...     -175.486833   
3      [0.977991372328468, 0.20481141277070392, -0.00...     -175.486833   
4      [0.977991372328468, 0.20481141277070392, -0.00...     -175.486833   
...                                                  ...             ...   
11760  [0.9779901014166766, 0.20492386078744854, -0.0...     -175.559252   
11761  [0.9779901014166766, 0.20492386078744854, -0.0...     -175.559252   
11762  [0.9779901014166766, 0.20492386078744854, -0.0...     -175.559252   
11763  [0.9779901014166766, 0.20492386078744854, -0.0...     -175.559252   
11764  [0.9780392824448754, 0.20459110634375524, -0.0...     -175.496496   

       camera-euler-y  camera-euler-z  
0           -0.677043       23.629267  
1           -0.677043       23.629267  
2           -0.677043       23.629267  
3           -0.677043       23.629267  
4           -0.677043       23.629267  
...               ...             ...  
11760       -0.730736       23.640265  
11761       -0.730736       23.640265  
11762       -0.730736       23.640265  
11763       -0.730736       23.640265  
11764       -0.706631       23.602306  

[11765 rows x 9 columns]

In [6]:
# subtract the average from each axis
df_mod = df.copy()
#ignore the first 1000 samples
df_mod = df_mod[6000:]
#limit to 10000 samples
df_mod = df_mod[:10000]
df_mod['timestamp'] = pd.to_datetime(df_mod['timestamp'], unit='s')
#convert all values to float
df_mod['imu-euler-x'] = df_mod['imu-euler-x'].astype(float)
df_mod['imu-euler-y'] = df_mod['imu-euler-y'].astype(float)
df_mod['imu-euler-z'] = df_mod['imu-euler-z'].astype(float)
df_mod['camera-euler-x'] = df_mod['camera-euler-x'].astype(float)
df_mod['camera-euler-y'] = df_mod['camera-euler-y'].astype(float)
df_mod['camera-euler-z'] = df_mod['camera-euler-z'].astype(float)

# get the average for each axis in euler
imu_euler_x_avg = df_mod['imu-euler-x'].mean()
imu_euler_y_avg = df_mod['imu-euler-y'].mean()
imu_euler_z_avg = df_mod['imu-euler-z'].mean()
camera_euler_x_avg = df_mod['camera-euler-x'].mean()
camera_euler_y_avg = df_mod['camera-euler-y'].mean()
camera_euler_z_avg = df_mod['camera-euler-z'].mean()
df_mod['imu-euler-x'] = df_mod['imu-euler-x'] - imu_euler_x_avg
df_mod['imu-euler-y'] = df_mod['imu-euler-y'] - imu_euler_y_avg
df_mod['imu-euler-z'] = df_mod['imu-euler-z'] - imu_euler_z_avg
df_mod['camera-euler-x'] = df_mod['camera-euler-x'] - camera_euler_x_avg
df_mod['camera-euler-y'] = df_mod['camera-euler-y'] - camera_euler_y_avg
df_mod['camera-euler-z'] = df_mod['camera-euler-z'] - camera_euler_z_avg


# plot 3 axis in the same plot
fig = px.line(df_mod, x='timestamp', y=['imu-euler-x', 'imu-euler-y', 'imu-euler-z', 'camera-euler-x', 'camera-euler-y', 'camera-euler-z'])
fig.show()
#save fig as html
plot_name = 'imu_euler_camera.html'
fig.write_html(plot_name)

In [7]:
#plot the histogram of each axis
for axis in ['imu-euler-x', 'imu-euler-y', 'imu-euler-z']:
    fig = px.histogram(df_mod, x=axis, nbins=100)
    fig.show()
    plot_name = f'{axis}_histogram_no_camera.html'
    fig.write_html(plot_name)